In [13]:
## Needed
# !pip install dali-dataset

---------------------
This notebook creates several batches of data. 
- /DALI-chunks-lines
    - Contains short (<30s) vocals on segments. Each track has a csv (found in /DALI-line-dicts) containing a transcript of each line-level subtrack and its filename, along with word-level relative timestamps for each subtrack. This is suitable for training whisper with timestamp output
- /DALI-chunks-pars
    - Paragraph-level vocals-only segments from each DALI track. See paragraphs.csv for transcriptions and file names. Suitable for training any ASR model that does not output word-level timestamps directly. From investigation there may be issues with correctness of the transcripts.
- There is additional a script to download via the youtube links the DALI audio tracks. dali_code has this built in, but it was not working for me


ISSUES:
- Transcriptions (word-, line-, and paragraph-level) are not necessarily written in correct english. Words are split or concatenated in unexpected ways. This needs addressing

---------
1. Investigate structure of dali data.

In [2]:
import DALI as dali_code
import pandas as pd
import os
import re
from pydub import AudioSegment

In [3]:
# Relative path to DALI folder
path = "../DALI_v1.0"

# Import DALI dataset
full_path = os.path.abspath(path)
dali_data = dali_code.get_the_DALI_dataset(full_path, skip=[], keep=[])

# Get info
dali_info_path = os.path.join(full_path, 'info/DALI_DATA_INFO.gz')
dali_info = dali_code.get_info(dali_info_path)

print(dali_info)

[['DALI_ID' 'NAME' 'YOUTUBE' 'WORKING']
 ['e186227bb7474fa5a7738c9108f11972' 'Staind-Tangled_Up_In_You'
  'NXG-ayocugI' 'True']
 ['520f583def024997adcab0567fb25a5d' 'Boyzone-Baby_Can_I_Hold_You'
  'ZjSLNZ9MsMI' 'True']
 ...
 ['e64aed27b6d64630985a5bc2ad571383'
  'Green_Day-Good_Riddance_(Time_Of_Your_Life)' '_bTdLi0YUVM' 'True']
 ['a8d53be9df7f41d58b3c7e404c8fc228'
  'Elton_John-Can_You_Feel_The_Love_Tonight?' 'KjgWWjkNbhU' 'True']
 ['a8bd4850b7f14f61bd745a5c82a899f8' 'Blink_182-Man_Overboard'
  'JyNqLOBlkFk' 'True']]


In [4]:
# Make a dataframe for easier viewing
df_DALI = pd.DataFrame(dali_info[1:], columns=dali_info[0])

df_DALI

DALI_ID  \
0     e186227bb7474fa5a7738c9108f11972   
1     520f583def024997adcab0567fb25a5d   
2     0f46aeae45ed4e6987f8b35e40d96c59   
3     f0226382730a4d339283c0e2cfaad43b   
4     3d45ce1696a14969b02b462f52a46d26   
...                                ...   
5353  32ad32c5688440e38398d86cc180db8d   
5354  5a80665694cb45829090fbfe40fb9ea6   
5355  e64aed27b6d64630985a5bc2ad571383   
5356  a8d53be9df7f41d58b3c7e404c8fc228   
5357  a8bd4850b7f14f61bd745a5c82a899f8   

                                               NAME      YOUTUBE WORKING  
0                          Staind-Tangled_Up_In_You  NXG-ayocugI    True  
1                       Boyzone-Baby_Can_I_Hold_You  ZjSLNZ9MsMI    True  
2                   The_Killers-For_Reasons_Unknown  TG5X4kOjEX8    True  
3             Olivia_Newton_John-A_Little_More_Love  4RFK8Ft-GNQ    True  
4               Magtens_Korridorer-Nordhavn_Station  aJCOAZMn9pU    True  
...                                             ...          ...     ...  
5353                         BoA-Listen_To_My_Heart  cK3qpJfb7w8    True  
5354  Carly_Rae_Jepsen-Tonight_I'm_Getting_Over_You  -XuqO7hOF4M    True  
5355    Green_Day-Good_Riddance_(Time_Of_Your_Life)  _bTdLi0YUVM    True  
5356      Elton_John-Can_You_Feel_The_Love_Tonight?  KjgWWjkNbhU    True  
5357                        Blink_182-Man_Overboard  JyNqLOBlkFk    True  

[5358 rows x 4 columns]

In [6]:
df_DALI['DALI_ID']

0       e186227bb7474fa5a7738c9108f11972
1       520f583def024997adcab0567fb25a5d
2       0f46aeae45ed4e6987f8b35e40d96c59
3       f0226382730a4d339283c0e2cfaad43b
4       3d45ce1696a14969b02b462f52a46d26
                      ...               
5353    32ad32c5688440e38398d86cc180db8d
5354    5a80665694cb45829090fbfe40fb9ea6
5355    e64aed27b6d64630985a5bc2ad571383
5356    a8d53be9df7f41d58b3c7e404c8fc228
5357    a8bd4850b7f14f61bd745a5c82a899f8
Name: DALI_ID, Length: 5358, dtype: object

In [7]:
df_DALI[df_DALI['DALI_ID']=='50e11b8e44024823ae9fe4bc38d18ea5']

DALI_ID               NAME      YOUTUBE WORKING
2299  50e11b8e44024823ae9fe4bc38d18ea5  KoRn-Here_To_Stay  Ft-7at-gNTU    True

In [8]:
entry = dali_data['50e11b8e44024823ae9fe4bc38d18ea5']
entry.info

{'dataset_version': 1.0,
 'ground-truth': False,
 'artist': 'KoRn',
 'title': 'Here To Stay',
 'scores': {'NCC': 0.9200032203657332, 'manual': 0.0},
 'audio': {'url': 'Ft-7at-gNTU', 'path': 'None', 'working': True},
 'id': '50e11b8e44024823ae9fe4bc38d18ea5',
 'metadata': {'album': 'Untouchables',
  'release_date': '2002',
  'cover': 'https://e-cdns-images.dzcdn.net/images/cover/6999e41d627f501bf0b588860405e2c7/1000x1000-000000-80-0-0.jpg',
  'genres': ['Pop', 'Metal'],
  'language': 'english'}}

In [ ]:
entry.annotations['annot']['lines']
#entry.annotations['annot']['words'] # For word-level time stamps
#entry.annotations['annot']['paragraphs'] # For larger chunks

[{'text': 'this time, taking it away',
  'freq': [440.0, 698.4564628660078],
  'time': [51.513999999999996, 53.913999999999994],
  'index': 0},
 {'text': "i've got a problem,",
  'freq': [523.2511306011972, 523.2511306011972],
  'time': [54.214, 56.013999999999996],
  'index': 0},
 {'text': 'with me getting in the way,',
  'freq': [523.2511306011972, 587.3295358348151],
  'time': [56.31399999999999, 58.788999999999994],
  'index': 0},
 {'text': 'not by design.',
  'freq': [440.0, 698.4564628660078],
  'time': [59.31399999999999, 60.81399999999999],
  'index': 0},
 {'text': 'so i take my face and',
  'freq': [440.0, 698.4564628660078],
  'time': [61.11399999999999, 63.21399999999999],
  'index': 0},
 {'text': 'bash it into a mirror.',
  'freq': [523.2511306011972, 587.3295358348151],
  'time': [63.21399999999999, 65.689],
  'index': 0},
 {'text': "i won't have to see the pain",
  'freq': [523.2511306011972, 587.3295358348151],
  'time': [65.91399999999999, 68.61399999999999],
  'index':

----------
2. Create line-level datasets

In [4]:
def remove_punctuation(s):
    s = re.sub(r'[^a-zA-Z0-9\s]', '', s)
    s = re.sub(r'\s+', ' ', s).strip()
    return s.lower()

In [ ]:
to_add = []

## Turn lyrics into dataframe
for d in entry.annotations['annot']['words']:
    word = d['text']
    start = d['time'][0]
    end = d['time'][1]
    to_add.append([word, start, end])

df_entry = pd.DataFrame(to_add, columns=['word', 'start', 'end'])
df_entry

# # save lyrics to df
# file_name = f"../DALI-audio/{entry.info['id']}/lyrics.csv"
# os.makedirs(f"../DALI-audio/{entry.info['id']}", exist_ok=True)

# df_entry.to_csv(os.path.abspath(file_name), index=False)

word       start         end
0        so   11.108000   11.221264
1    sorry,   11.259018   12.127373
2      it's   12.316146   12.429410
3      over   12.467165   15.449776
4        so   16.091603   16.204867
..      ...         ...         ...
234    yeah  156.010046  156.198818
235   later  156.312082  156.802892
236     see  157.218192  157.406965
237     you  157.520228  157.709001
238  around  157.822265  159.068166

[239 rows x 3 columns]

---------------------
Creating the timestamped lyrics dataset

In [ ]:
## Use line-level lyrics from DALI to create small chunks the lyrics from each track
## these are saved to their own dictionary

dir_path = "C:\\Users\\dacla\\Documents\\DALI-line-dicts" 
lens = []

for dali_id in df_DALI['DALI_ID']:
    entry = dali_data[dali_id]

    to_add = []

    for d in entry.annotations['annot']['lines']:
        words = d['text']
        words = words.replace(' - ', ' ')
        words = words.replace('- ', ' ')
        words = words.replace('-', ' ')
        words = remove_punctuation(words) 
        
        start = round(d['time'][0], 3)
        end = round(d['time'][1], 3)

        l = end - start
        if l < 0 or l > 30:
            continue
        
        to_add.append([words, start, end])

    df_lines = pd.DataFrame(to_add, columns=['words', 'start', 'end'])
    df_lines.to_csv(os.path.join(dir_path, f"{dali_id}.csv"), index=False)


The following cell takes a **long** time to run. 

In [ ]:
import demucs.separate
from pydub import AudioSegment
from tqdm import tqdm

## Split the vocals stem off using demucs. Then save the portions of the vocals track at a given list of times 
## These times should come from the df_lines dataframes

def extract_portions(times):
    # Define path names for demucs
    demucs_path = os.path.abspath(f"separated/mdx_extra/{root}")
    vocals_path = os.path.join(demucs_path, "vocals.wav")
    no_vocals_path = os.path.join(demucs_path, "no_vocals.wav")

    demucs.separate.main(["--two-stems", "vocals", "-n", "mdx_extra", audio_path])

    audio = AudioSegment.from_file(vocals_path)

    if audio.channels > 1:
        audio = audio.set_channels(1)

    if audio.frame_rate != 16000:
        audio = audio.set_frame_rate(16000)

    segment_names = []

    for i in range(len(times)):
        start = times[i][0] * 1000
        end = times[i][1] * 1000

        # Split the portion that contains vocals
        portion = audio[start:end]

        # Keep in order
        portion.export(f"T:\\chunked\\{dali_id}-{i}.wav", format="wav")
        segment_names.append(f'{dali_id}-{i}.wav')
    
    # Delete splits
    os.remove(vocals_path)
    os.remove(no_vocals_path)
    os.rmdir(demucs_path)

    return segment_names

# Replace with your path
dali_audio = "T:\\DALI-audio"
output_path = "T:\\chunked"


for dali_id in tqdm(os.listdir(dali_audio)):
    entry = dali_data[dali_id]

    df = pd.read_csv(os.path.join(dir_path, f"{dali_id}.csv"))

    for file in os.listdir(os.path.join(dali_audio, dali_id)):
        root, ext = os.path.splitext(file)

        if ext == '.wav':
            audio_path = f"T:\\DALI-audio\\{dali_id}\\{file}"
            break

    times = []

    for row in df.itertuples():
        start = row[2]
        end = row[3]
        times.append([start, end])

    file_names = extract_portions(times)

    # Add the file names to the lyrics dfs
    df['files'] = file_names
    df.to_csv(os.path.join(dir_path, f"{dali_id}.csv"), index=False)

  0%|          | 0/3261 [00:00<?, ?it/s]

Selected model is a bag of 4 models. You will see that many progress bars per track.
Separated tracks will be stored in C:\Users\dacla\Documents\auto-censoring-local\separated\mdx_extra
Separating track T:\DALI-audio\001940b614eb43f4a0c826d49a67d66d\woman-in-love.wav


100%|███████████████████████████████████████████████████████████████████████| 231.0/231.0 [00:02<00:00, 103.40seconds/s]
100%|███████████████████████████████████████████████████████████████████████| 231.0/231.0 [00:02<00:00, 101.22seconds/s]
100%|████████████████████████████████████████████████████████████████████████| 231.0/231.0 [00:02<00:00, 99.79seconds/s]
100%|███████████████████████████████████████████████████████████████████████| 231.0/231.0 [00:02<00:00, 102.31seconds/s]
  0%|          | 1/3261 [00:12<11:20:22, 12.52s/it]

Selected model is a bag of 4 models. You will see that many progress bars per track.
Separated tracks will be stored in C:\Users\dacla\Documents\auto-censoring-local\separated\mdx_extra
Separating track T:\DALI-audio\0056b60ad09c4f389d107868e2d5c149\its-my-lifeconfessions-pt-ii.wav


100%|███████████████████████████████████████████████████████████████████████| 198.0/198.0 [00:01<00:00, 106.84seconds/s]
100%|███████████████████████████████████████████████████████████████████████| 198.0/198.0 [00:01<00:00, 112.77seconds/s]
100%|███████████████████████████████████████████████████████████████████████| 198.0/198.0 [00:01<00:00, 110.72seconds/s]
100%|███████████████████████████████████████████████████████████████████████| 198.0/198.0 [00:01<00:00, 115.05seconds/s]
  0%|          | 2/3261 [00:22<10:00:08, 11.05s/it]

...

100%|████████████████████████████████████████████████████████████████████████| 231.0/231.0 [00:02<00:00, 93.96seconds/s]
100%|████████████████████████████████████████████████████████████████████████| 231.0/231.0 [00:02<00:00, 95.21seconds/s]
100%|████████████████████████████████████████████████████████████████████████| 231.0/231.0 [00:02<00:00, 93.20seconds/s]
100%|████████████████████████████████████████████████████████████████████████| 231.0/231.0 [00:02<00:00, 90.13seconds/s]
 42%|████▏     | 1372/3261 [4:49:55<7:11:23, 13.70s/it]

Selected model is a bag of 4 models. You will see that many progress bars per track.
Separated tracks will be stored in C:\Users\dacla\Documents\auto-censoring-local\separated\mdx_extra
Separating track T:\DALI-audio\6a3be17d5861426a8f04c7916baa5a5d\babylon.wav


100%|████████████████████████████████████████████████████████████████████████| 264.0/264.0 [00:02<00:00, 95.03seconds/s]
100%|████████████████████████████████████████████████████████████████████████| 264.0/264.0 [00:02<00:00, 95.58seconds/s]
100%|████████████████████████████████████████████████████████████████████████| 264.0/264.0 [00:02<00:00, 95.39seconds/s]
100%|████████████████████████████████████████████████████████████████████████| 264.0/264.0 [00:02<00:00, 98.66seconds/s]
 42%|████▏     | 1373/3261 [4:50:10<7:19:09, 13.96s/it]

Selected model is a bag of 4 models. You will see that many progress bars per track.
Separated tracks will be stored in C:\Users\dacla\Documents\auto-censoring-local\separated\mdx_extra
Separating track T:\DALI-audio\6a50146df2344c0cac2b1e7a1d8022fb\the-climb.wav


100%|████████████████████████████████████████████████████████████████████████| 231.0/231.0 [00:02<00:00, 88.39seconds/s]
100%|████████████████████████████████████████████████████████████████████████| 231.0/231.0 [00:02<00:00, 89.00seconds/s]
100%|████████████████████████████████████████████████████████████████████████| 231.0/231.0 [00:02<00:00, 88.16seconds/s]


Create the word level timestamps for each of the chunks

In [ ]:
for dali_id in os.listdir(dali_audio):
    entry = dali_data[dali_id]
    
    df_words = pd.read_csv(f"T:\\DALI-audio\\{dali_id}\\lyrics.csv") #Load lyrics dfs from earlier, or use dali_dataset directly
    df_lines = pd.read_csv(os.path.join(dir_path, f"{dali_id}.csv"))
    
    to_add = []

    for row in df_lines.itertuples():
        start = row[2]
        end = row[3]

        # Use the times of the word-level transcripts to select the portion
        df = df_words[(df_words['start'] >= start) & (df_words['end'] <= end)].copy()

        # Create relative times within the extracted audio clip
        df['start'] = round(df['start'] - start, 3)
        df['end'] = round(df['end'] - start, 3)

        # Whisper expects timestamped lyrics to be of this form {word: str, start: flt, end: flt}
        to_add.append(df.to_dict(orient='records'))
        
    df_lines['transcript'] = to_add
    df_lines.to_csv(os.path.join(dir_path, f"{dali_id}.csv"), index=False)


----------------

----------------
3. This portion is for downloading the audio tracks from youtube. It also takes awhile

In [2]:
import yt_dlp

def download_youtube_audio(url, filename, output_path='.', file_format='mp3'):
    """
    Downloads audio from a YouTube URL.

    Args:
        url (str): The YouTube video URL.
        output_path (str): The directory to save the audio file.
        file_format (str): The desired audio format (e.g., 'mp3', 'wav', 'm4a', 'opus').
    """
    # Create the output directory if it doesn't exist
    os.makedirs(output_path, exist_ok=True)

    ## ffmpeg location varies by operating system...
    if os.name == 'nt':
        ffmpeg_loc = "C:\\ffmpeg\\bin\\"

    elif os.name == 'posix':
        ffmpeg_loc = "/opt/anaconda3/bin/ffmpeg"
    
    ydl_opts = {
        'format': 'bestaudio/best',  # Download the best available audio format
        'outtmpl': os.path.join(output_path, f"{filename}"), # Output file template
        'postprocessors': [{
            'key': 'FFmpegExtractAudio', # Use FFmpeg to extract audio
            'preferredcodec': file_format, # Preferred audio codec
            'preferredquality': '0',     # Best quality
        }],
        'ffmpeg_location': ffmpeg_loc,
        'quiet': True, # Turns off text info
    }

    try:
        with yt_dlp.YoutubeDL(ydl_opts) as ydl:
            info_dict = ydl.extract_info(url, download=True)
            #title = info_dict.get('title', 'unknown_title')
            #print(f"Successfully downloaded: {filename}.{file_format}")
            return os.path.join(output_path, f"{filename}.{file_format}") # Return the downloaded file path
        
    except yt_dlp.DownloadError as e:
        print(f"Error downloading audio: {e}")
        return None
    
    except Exception as e:
        print(f"An unexpected error occurred: {e}")
        return None


Apply to the whole dataset (it will take awhile)

In [ ]:
## Now do it all in one go
for entry_id in df['DALI_ID']:
    
    entry = dali_data[entry_id]
    output_dir = os.path.abspath(f"../DALI-audio/{entry.info['id']}")
    
    fname = remove_punctuation(entry.info['title']).replace(" ", "-") ### Check this

    ## Create directory
    os.makedirs(output_dir, exist_ok=True)

    ## Get audio
    youtube_url = entry.info['audio']['url']

    downloaded_file = download_youtube_audio(url=youtube_url, 
                                            filename=fname,
                                            output_path=output_dir,
                                            file_format='wav')

    # If the youtube download fails remove the directory and continue
    if not downloaded_file:
        os.rmdir(output_dir)
        continue
    
    # ## Turn lyrics into dataframe -- DONE ALREADY NOT NEEDED
    # to_add = []
    # for d in entry.annotations['annot']['words']:
    #     word = remove_punctuation(d['text'])
        
    #     start = d['time'][0]
    #     end = d['time'][1]

    #     to_add.append([word, start, end])

    # df_entry = pd.DataFrame(to_add, columns=['word', 'start', 'end'])

    # # Save lyrics to df
    # df_entry.to_csv(os.path.abspath(f"../DALI-audio/{entry.info['id']}/lyrics.csv"), index=False)
    
    ## Save metadata
    save_dictionary(entry.info, os.path.abspath(f"../DALI-audio/{entry.info['id']}/metadata.pkl"))

[youtube] Extracting URL: NXG-ayocugI
[youtube] NXG-ayocugI: Downloading webpage
[youtube] NXG-ayocugI: Downloading tv client config
[youtube] NXG-ayocugI: Downloading tv player API JSON
[youtube] NXG-ayocugI: Downloading ios player API JSON
[youtube] NXG-ayocugI: Downloading m3u8 information
[info] NXG-ayocugI: Downloading 1 format(s): 251
[download] Destination: ..\DALI-audio\e186227bb7474fa5a7738c9108f11972\tangled-up-in-you
[download] 100% of    4.77MiB in 00:00:00 at 19.04MiB/s    
[ExtractAudio] Destination: ..\DALI-audio\e186227bb7474fa5a7738c9108f11972\tangled-up-in-you.wav
Deleting original file ..\DALI-audio\e186227bb7474fa5a7738c9108f11972\tangled-up-in-you (pass -k to keep)
[youtube] Extracting URL: ZjSLNZ9MsMI
[youtube] ZjSLNZ9MsMI: Downloading webpage
[youtube] ZjSLNZ9MsMI: Downloading tv client config
[youtube] ZjSLNZ9MsMI: Downloading tv player API JSON
[youtube] ZjSLNZ9MsMI: Downloading ios player API JSON
[youtube] ZjSLNZ9MsMI: Downloading m3u8 information
[info] ZjSL

ERROR: [youtube] aJCOAZMn9pU: Video unavailable


Error downloading audio: ERROR: [youtube] aJCOAZMn9pU: Video unavailable
Doesn't exit, skipping
[youtube] Extracting URL: lEUy2cGJwG0
[youtube] lEUy2cGJwG0: Downloading webpage
[youtube] lEUy2cGJwG0: Downloading tv client config
[youtube] lEUy2cGJwG0: Downloading tv player API JSON
[youtube] lEUy2cGJwG0: Downloading ios player API JSON


ERROR: [youtube] lEUy2cGJwG0: Video unavailable. This video is no longer available because the YouTube account associated with this video has been terminated.


Error downloading audio: ERROR: [youtube] lEUy2cGJwG0: Video unavailable. This video is no longer available because the YouTube account associated with this video has been terminated.
Doesn't exit, skipping
[youtube] Extracting URL: PbVYg0EVpek
[youtube] PbVYg0EVpek: Downloading webpage
[youtube] PbVYg0EVpek: Downloading tv client config
[youtube] PbVYg0EVpek: Downloading tv player API JSON
[youtube] PbVYg0EVpek: Downloading ios player API JSON


...

ERROR: [youtube] CIYS9EQWkXg: Video unavailable. This video is no longer available because the YouTube account associated with this video has been terminated.


Error downloading audio: ERROR: [youtube] CIYS9EQWkXg: Video unavailable. This video is no longer available because the YouTube account associated with this video has been terminated.
Doesn't exit, skipping
[youtube] Extracting URL: ACp-kVgV0Iw
[youtube] ACp-kVgV0Iw: Downloading webpage
[youtube] ACp-kVgV0Iw: Downloading tv client config
[youtube] ACp-kVgV0Iw: Downloading tv player API JSON
[youtube] ACp-kVgV0Iw: Downloading ios player API JSON
[youtube] ACp-kVgV0Iw: Downloading m3u8 information
[info] ACp-kVgV0Iw: Downloading 1 format(s): 251
[download] Destination: ..\DALI-audio\81275468fa124185a222bf037764e925\ring-of-steel
[download] 100% of    6.35MiB in 00:00:00 at 18.29MiB/s  
[ExtractAudio] Destination: ..\DALI-audio\81275468fa124185a222bf037764e925\ring-of-steel.wav
Deleting original file ..\DALI-audio\81275468fa124185a222bf037764e925\ring-of-steel (pass -k to keep)
[youtube] Extracting URL: bzYHbPkrMzw
[youtube] bzYHbPkrMzw: Downloading webpage
[youtube] bzYHbPkrMzw: Download

ERROR: [youtube] iIWHIvaK7DA: Video unavailable. This video is no longer available due to a copyright claim by Ex Noctem Nacimur Music


Error downloading audio: ERROR: [youtube] iIWHIvaK7DA: Video unavailable. This video is no longer available due to a copyright claim by Ex Noctem Nacimur Music
Doesn't exit, skipping
[youtube] Extracting URL: xntxoEFsqfU
[youtube] xntxoEFsqfU: Downloading webpage
[youtube] xntxoEFsqfU: Downloading tv client config
[youtube] xntxoEFsqfU: Downloading tv player API JSON
[youtube] xntxoEFsqfU: Downloading ios player API JSON
[youtube] xntxoEFsqfU: Downloading m3u8 information
[info] xntxoEFsqfU: Downloading 1 format(s): 251
[download] Destination: ..\DALI-audio\3852f692f72e4c43bbcdb6fe021ea087\ill-be-waiting
[download] 100% of    4.35MiB in 00:00:00 at 18.92MiB/s  
[ExtractAudio] Destination: ..\DALI-audio\3852f692f72e4c43bbcdb6fe021ea087\ill-be-waiting.wav
Deleting original file ..\DALI-audio\3852f692f72e4c43bbcdb6fe021ea087\ill-be-waiting (pass -k to keep)
[youtube] Extracting URL: bhUTNN7AB6k
[youtube] bhUTNN7AB6k: Downloading webpage
[youtube] bhUTNN7AB6k: Downloading tv client config


[youtube] bhUTNN7AB6k: Downloading m3u8 information
[info] bhUTNN7AB6k: Downloading 1 format(s): 234
[hlsnative] Downloading m3u8 manifest
[hlsnative] Total fragments: 41
[download] Destination: ..\DALI-audio\f1d78243e60346cca09a17468220e6c8\angus-mcfife
[download] 100% of    3.28MiB in 00:00:01 at 2.10MiB/s                   
[ExtractAudio] Destination: ..\DALI-audio\f1d78243e60346cca09a17468220e6c8\angus-mcfife.wav
Deleting original file ..\DALI-audio\f1d78243e60346cca09a17468220e6c8\angus-mcfife (pass -k to keep)
[youtube] Extracting URL: OQHtHowsRC4
[youtube] OQHtHowsRC4: Downloading webpage
[youtube] OQHtHowsRC4: Downloading tv client config
[youtube] OQHtHowsRC4: Downloading tv player API JSON
[youtube] OQHtHowsRC4: Downloading ios player API JSON
[youtube] OQHtHowsRC4: Downloading m3u8 information
[info] OQHtHowsRC4: Downloading 1 format(s): 251
[download] Destination: ..\DALI-audio\1d87a1b3629f435c84ecd243e7fa6cb0\wishmaster-live
[download] 100% of    3.92MiB in 00:00:00 at 13.

-----------------------------

-----------------
4. Extract paragraph-level chunks of audio. Not recommended

In [ ]:
dali_dir = os.path.abspath(f"../DALI-audio")

for id in os.listdir(dali_dir):
    entry = dali_data[id]
    lyrics_par = []

    for d in entry.annotations['annot']['paragraphs']:
        words = d['text']
        
        words = words.replace(' - ', '')
        words = words.replace('- ', '')
        words = words.replace('-', ' ')
        words = remove_punctuation(words) 

        start = round(d['time'][0], 3)
        end = round(d['time'][1], 3)

        lyrics_par.append([words, start, end])

    df_par = pd.DataFrame(lyrics_par, columns=['words', 'start', 'end'])

    os.makedirs(f'../DALI-audio-chunks/{id}/', exist_ok=True)

    df_par.to_csv(f'../DALI-audio-chunks/{id}/lyrics-paragraphs.csv', index=False)


In [13]:
import os
import pandas as pd
from pydub import AudioSegment
import demucs.separate
import pickle

def extract_portions(id, input_audio_path, times):
    # Get path names for inputs
    root, ext = os.path.splitext(os.path.basename(input_audio_path))
    dir = os.path.dirname(input_audio_path)

    # Define path names for demucs
    demucs_path = os.path.abspath(f"separated/mdx_extra/{root}")
    vocals_path = os.path.join(demucs_path, "vocals.wav")
    no_vocals_path = os.path.join(demucs_path, "no_vocals.wav")

    # Do not rerun if not needed
    if not os.path.isfile(vocals_path):
        demucs.separate.main(["--two-stems", "vocals", "-n", "mdx_extra", input_audio_path])

    audio = AudioSegment.from_file(vocals_path)

    segment_names = []

    for i in range(len(times)):
        start = times[i][0] * 1000
        end = times[i][1] * 1000

        if start >= end:
            continue

        # Split the portion that contains vocals
        portion = audio[start:end]

        # Keep in order
        output_path = os.path.join("C:\\Users\\dacla\\Documents\\DALI-chunks", f"{id}-{i}.mp3")
        portion.export(output_path, format="mp3")

        segment_names.append(output_path)
    
    # Delete splits
    os.remove(vocals_path)
    os.remove(no_vocals_path)
    os.rmdir(demucs_path)

    return segment_names

dali_dir = os.path.abspath(f"../DALI-audio")
lyrics_dict = dict()

for id in os.listdir(dali_dir):
    for file in os.listdir(os.path.join(dali_dir, id)):
        root, ext = os.path.splitext(file)

        if ext == '.mp3':
            audio_path = os.path.join(os.path.join(dali_dir, id), file)

    df = pd.read_csv(f"../DALI-audio/{id}/lyrics-paragraphs.csv")

    times = []
    for row in df.itertuples():
        start = row[2]
        end = row[3]
        times.append([start, end])

    extract_portions(id=id, input_audio_path=audio_path, times=times)
    lyrics_dict[id] = df

    # it's not necessary but update the dict everytime
    with open("lyrics-full.pkl", "wb") as f:
        pickle.dump(lyrics_dict, f)

Selected model is a bag of 4 models. You will see that many progress bars per track.
Separated tracks will be stored in C:\Users\dacla\Documents\auto-censoring-local\separated\mdx_extra
Separating track c:\Users\dacla\Documents\DALI-audio\001940b614eb43f4a0c826d49a67d66d\woman-in-love.mp3


100%|███████████████████████████████████████████████████████████████████████| 231.0/231.0 [00:02<00:00, 102.39seconds/s]
100%|███████████████████████████████████████████████████████████████████████| 231.0/231.0 [00:02<00:00, 101.57seconds/s]
100%|████████████████████████████████████████████████████████████████████████| 231.0/231.0 [00:02<00:00, 97.52seconds/s]
100%|███████████████████████████████████████████████████████████████████████| 231.0/231.0 [00:02<00:00, 106.79seconds/s]


Selected model is a bag of 4 models. You will see that many progress bars per track.
Separated tracks will be stored in C:\Users\dacla\Documents\auto-censoring-local\separated\mdx_extra
Separating track c:\Users\dacla\Documents\DALI-audio\0056b60ad09c4f389d107868e2d5c149\its-my-lifeconfessions-pt-ii.mp3


100%|███████████████████████████████████████████████████████████████████████| 198.0/198.0 [00:01<00:00, 105.24seconds/s]
100%|███████████████████████████████████████████████████████████████████████| 198.0/198.0 [00:01<00:00, 109.54seconds/s]
100%|███████████████████████████████████████████████████████████████████████| 198.0/198.0 [00:01<00:00, 106.66seconds/s]
100%|███████████████████████████████████████████████████████████████████████| 198.0/198.0 [00:01<00:00, 112.97seconds/s]


Selected model is a bag of 4 models. You will see that many progress bars per track.
Separated tracks will be stored in C:\Users\dacla\Documents\auto-censoring-local\separated\mdx_extra
Separating track c:\Users\dacla\Documents\DALI-audio\007c0152242340008ff45781a9b08546\wildfire.mp3


...

100%|███████████████████████████████████████████████████████████████████████| 231.0/231.0 [00:02<00:00, 110.74seconds/s]
100%|███████████████████████████████████████████████████████████████████████| 231.0/231.0 [00:01<00:00, 117.63seconds/s]
100%|███████████████████████████████████████████████████████████████████████| 231.0/231.0 [00:01<00:00, 118.93seconds/s]
100%|███████████████████████████████████████████████████████████████████████| 231.0/231.0 [00:01<00:00, 123.83seconds/s]


Selected model is a bag of 4 models. You will see that many progress bars per track.
Separated tracks will be stored in C:\Users\dacla\Documents\auto-censoring-local\separated\mdx_extra
Separating track c:\Users\dacla\Documents\DALI-audio\fff82259df19459aaf61a0814d9f6453\you-oughta-know.mp3


100%|███████████████████████████████████████████████████████████████████████| 231.0/231.0 [00:02<00:00, 101.47seconds/s]
100%|███████████████████████████████████████████████████████████████████████| 231.0/231.0 [00:02<00:00, 111.85seconds/s]
100%|███████████████████████████████████████████████████████████████████████| 231.0/231.0 [00:02<00:00, 109.01seconds/s]
100%|███████████████████████████████████████████████████████████████████████| 231.0/231.0 [00:02<00:00, 113.15seconds/s]


Selected model is a bag of 4 models. You will see that many progress bars per track.
Separated tracks will be stored in C:\Users\dacla\Documents\auto-censoring-local\separated\mdx_extra
Separating track c:\Users\dacla\Documents\DALI-audio\fffdba22ae1647a2910541b4d4ec3bed\get-into-the-groove.mp3


100%|███████████████████████████████████████████████████████████████████████| 297.0/297.0 [00:02<00:00, 104.65seconds/s]
100%|███████████████████████████████████████████████████████████████████████| 297.0/297.0 [00:02<00:00, 107.54seconds/s]
100%|███████████████████████████████████████████████████████████████████████| 297.0/297.0 [00:02<00:00, 107.18seconds/s]
100%|███████████████████████████████████████████████████████████████████████| 297.0/297.0 [00:02<00:00, 110.35seconds/s]


----------------
Create a master list of paragraph level chunks. This is "metadata.csv". Does not have timestamps for word-level data. 

In [11]:
import pickle

with open("lyrics-full.pkl", "wb") as f:
    pickle.dump(lyrics_dict, f)

In [ ]:
# Combine all transcripts as one csv with audio paths
dali_dir = os.path.abspath(f"../DALI-audio")

df_data = pd.DataFrame(columns=['file', 'transcript'])

for id in os.listdir(dali_dir):
    df = pd.read_csv(f"../DALI-audio/{id}/lyrics-paragraphs.csv")

    l = []
    for i, row in enumerate(df.itertuples()):
        trans = row[1] 

        if row[2] >= row[3]:
            continue
        
        file_name = f'{id}-{i}.mp3'
        l.append([file_name, trans])
    
    df_temp = pd.DataFrame(l, columns=['file', 'transcript'])
    df_data = pd.concat([df_data, df_temp])

-------------------------
Master list for word level data

In [ ]:
import os
import pandas as pd

dir_wavs = "T:\\dl-project\\DALI-chunks-lines"
dir_dicts = "C:\\Users\\dacla\\Documents\\auto-censoring-local\\DALI-line-dicts"

df_full = pd.DataFrame(columns=['filename', 'words', 'transcript'])

for file in os.listdir(dir_dicts):
    df = pd.read_csv(os.path.join(dir_dicts, file))
    
    cols = df.columns.tolist()

    # Skip songs that weren't used
    if 'transcript' not in cols:
        continue
    
    to_add = []

    # My indexing wasn't consistent...
    trans_ind = cols.index('words') + 1
    times_ind = cols.index('transcript') + 1
    fname_ind = cols.index('files') + 1

    for row in df.itertuples():
        filename = row[fname_ind]
        word_timestamps = row[times_ind]
        transcript = row[trans_ind]

        to_add.append([filename, word_timestamps, transcript])

    df_temp = pd.DataFrame(to_add, columns=['filename', 'words', 'transcript'])

    df_full = pd.concat([df_full, df_temp])


In [ ]:
# Find columns that are strings
is_str = df_full['transcript'].apply(lambda x: isinstance(x,str))

# Save the corrected dataset
df_full_filt = df_full[is_str]
df_full_filt.to_csv('metadata-word-level.csv', index=False)

## Observe the ones that failed
df_full[~is_str]

filename  \
0      13fa185d70534bc19b2ce69ddeb86489-0.wav   
1      13fa185d70534bc19b2ce69ddeb86489-1.wav   
43    13fa185d70534bc19b2ce69ddeb86489-43.wav   
31    140c6f74cc7e44efb29ef3348474e98c-31.wav   
35    23e03059ce3f49ecaabc05c0ba769c3e-35.wav   
165  27675f8bbd7b4c69acb0c9bae6e2ace1-165.wav   
18    2cadde3ca66b499cac8767907e307be6-18.wav   
33    2cadde3ca66b499cac8767907e307be6-33.wav   
38    38c7f272852a40f0a2e188c517edaa29-38.wav   
43    47e7dbeb662548149b97df1c226654c5-43.wav   
13    523d324b325f487aac86a2327b6f05ca-13.wav   
46    5529484c29a741cfbbabf403b9cd5539-46.wav   
17    55a1305f0b81431d8399e96a182a0ec8-17.wav   
32    60725a5ecd6f4605abac479d3cacbc98-32.wav   
81    62d88e2bb5a04ebc95ec5406a10fce0d-81.wav   
38    75ad1213a743497185a0b13cb11d4a37-38.wav   
65    7c4294f5d00945d6a05e7027333802a7-65.wav   
56    87b77a75197e40f4b324a6f0fe37bbca-56.wav   
70    91032fba762247b8a1c1f1256cc48023-70.wav   
41    9ae7c99571254d43a3bf3f17e920c276-41.wav   
29    a0d284b9488b4f60b7e9380e949ae54d-29.wav   
62    a54fd161e2f843d3b6cc15c7f8463d43-62.wav   
0      ae0b0ce90ab14ea5b5416cf44359d808-0.wav   
1      ae0b0ce90ab14ea5b5416cf44359d808-1.wav   
1      b73f0b7963974fb2a1f1bd51214cbe47-1.wav   
2      b73f0b7963974fb2a1f1bd51214cbe47-2.wav   
3      b73f0b7963974fb2a1f1bd51214cbe47-3.wav   
4      b73f0b7963974fb2a1f1bd51214cbe47-4.wav   
13    b73f0b7963974fb2a1f1bd51214cbe47-13.wav   
23    b73f0b7963974fb2a1f1bd51214cbe47-23.wav   
24    b73f0b7963974fb2a1f1bd51214cbe47-24.wav   
25    b73f0b7963974fb2a1f1bd51214cbe47-25.wav   
31    c18dc38628af4a81b688d65a69c43ab4-31.wav   
54    c18dc38628af4a81b688d65a69c43ab4-54.wav   
49    c3d4a30cfe1f4656b42b3e442e135be5-49.wav   
36    c3d6fdbc5a994de4bd013c4c926e5b90-36.wav   
0      ce44299649fd4fa1aabd39e70f7f4f15-0.wav   
1      d8eea83292c4428cbb45964e56e8dffc-1.wav   
2      d8eea83292c4428cbb45964e56e8dffc-2.wav   
3      d8eea83292c4428cbb45964e56e8dffc-3.wav   
4      d8eea83292c4428cbb45964e56e8dffc-4.wav   
5      d8eea83292c4428cbb45964e56e8dffc-5.wav   
51    dc2a92f520924fa5a1fbc3417f15b559-51.wav   
0      e533227ea8894685b38b6e894b0d3cfa-0.wav   
1      e533227ea8894685b38b6e894b0d3cfa-1.wav   
46    e533227ea8894685b38b6e894b0d3cfa-46.wav   

                                                 words transcript  
0                                                   []        NaN  
1          [{'word': nan, 'start': 0.0, 'end': 0.045}]        NaN  
43                                                  []        NaN  
31         [{'word': nan, 'start': 0.0, 'end': 0.084}]        NaN  
35   [{'word': nan, 'start': 0.0, 'end': 0.251}, {'...        NaN  
165                                                 []        NaN  
18                                                  []        NaN  
33         [{'word': nan, 'start': 0.0, 'end': 0.116}]        NaN  
38                                                  []        NaN  
43                                                  []        NaN  
13                                                  []        NaN  
46                                                  []        NaN  
17                                                  []        NaN  
32                                                  []        NaN  
81   [{'word': nan, 'start': 0.165, 'end': 0.494}, ...        NaN  
38                                                  []        NaN  
65                                                  []        NaN  
56         [{'word': nan, 'start': 0.0, 'end': 0.604}]        NaN  
70                                                  []        NaN  
41         [{'word': nan, 'start': 0.0, 'end': 3.917}]        NaN  
29                                                  []        NaN  
62                                                  []        NaN  
0    [{'word': nan, 'start': 0.0, 'end': 2.982}, {'...        NaN  
1    [{'word': nan, 'start': 0.0, 'end': 1.118}, {'...        NaN  
1    [{'word': nan, 'start': 0.0,